### Full of Features

#### Libraries

In [1]:
from sklearn.model_selection import cross_val_score
import numpy as np
import pandas as pd
from collections import defaultdict
from sklearn.model_selection import KFold
from sklearn.metrics import mean_squared_error
from math import sqrt
from catboost import CatBoostRegressor, Pool
import pickle

pd.set_option('display.max_columns', 500)

#### Load Data

In [2]:
data_dir = '/Users/konstantinivanov/Documents/work/PIK/files-pik_digital_day_final'
input_dir = '/Users/konstantinivanov/Documents/work/PIK/input'
output_dir = '/Users/konstantinivanov/Documents/work/PIK/output'
sub_dir = '/Users/konstantinivanov/Documents/work/PIK/sub'

#### Second Month - Matching start_square

In [8]:
train_data_lastfeb = pd.read_csv(input_dir + "/train_full_lastfeb.csv")
train_data_mar = pd.read_csv(sub_dir + "/subsub_full_feat_mer.csv")
test_data = pd.read_csv(data_dir + '/test.csv', encoding='cp1251')

In [12]:
len(train_data_lastfeb.columns)

48

In [19]:
train_data_lastfeb.shape

(9244, 48)

In [9]:
train_data_lastfeb.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

In [16]:
len(train_data_mar.columns)

48

In [20]:
train_data_mar.shape

(526, 48)

In [15]:
train_data_mar.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01        8547.7   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01       13471.7   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01        1136.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01        6598.0   
4  20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01         187.2   

         value          price  mean_sq  mean_fl  month  month_cnt  \
0   811.094601  147387.111111    37.99        9      3         39   
1  1259.443867  138465.811966    57.80        9      3         39   
2   188.162684  171589.583333    23.67       10      3         39   
3   645.633283  134381.707317    80.46        8      3         39   
4    18.758518  182700.000000    93.60        3      3         39   

  Класс объекта  Количество помещений Огорожена территория  \
0        эконом                  1983                  нет   
1        эконом                  1983                  нет   
2        эконом                  1983                  нет   
3        эконом                  1983                  нет   
4       комфорт                  1094                  нет   

   Площадь земельного участка Входные группы  Детский сад  Школа  Поликлиника  \
0                        17.0             да          345    825            0   
1                        17.0             да          345    825            0   
2                        17.0             да          345    825            0   
3                        17.0             да          345    825            0   
4                         6.8             да          150    550            0   

   ФОК Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  \
0    0       нет       да         да                  1           1   
1    0       нет       да         да                  1           1   
2    0       нет       да         да                  1           1   
3    0       нет       да         да                  1           1   
4    1       нет       да         да                  1           1   

   Видеонаблюдение Подземная парковка Двор без машин  Машиномест  \
0                0                 да             да        1800   
1                0                 да             да        1800   
2                0                 да             да        1800   
3                0                 да             да        1800   
4                1                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35

In [11]:
test_data

id                               bulk_id  spalen       date1  \
0        0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1        1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2        2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3        3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4        4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
5        5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
6        6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
7        7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
8        8  F07BF3C7-C905-E811-893D-00505688958B       2  2018-04-01   
9        9  F07BF3C7-C905-E811-893D-00505688958B       3  2018-04-01   
10      10  F07BF3C7-C905-E811-893D-00505688958B       0  2018-04-01   
11      11  F07BF3C7-C905-E811-893D-00505688958B       1  2018-04-01   
12      12  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-05-01   
13      13  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-05-01   
14      14  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-05-01   
15      15  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-05-01   
16      16  F07BF3C7-C905-E811-893D-00505688958B       2  2018-05-01   
17      17  F07BF3C7-C905-E811-893D-00505688958B       3  2018-05-01   
18      18  F07BF3C7-C905-E811-893D-00505688958B       0  2018-05-01   
19      19  F07BF3C7-C905-E811-893D-00505688958B       1  2018-05-01   
20      20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   
21      21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   
22      22  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-05-01   
23      23  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-03-01   
24      24  35168781-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
25      25  35168781-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
26      26  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-03-01   
27      27  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-03-01   
28      28  50B329EC-1DE2-E511-B953-001EC9D56418       3  2018-03-01   
29      29  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-03-01   
...    ...                                   ...     ...         ...   
1787  1787  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-04-01   
1788  1788  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-04-01   
1789  1789  999F708D-4FE9-E711-B9FF-00505688958B       4  2018-04-01   
1790  1790  999F708D-4FE9-E711-B9FF-00505688958B       3  2018-04-01   
1791  1791  AECE8386-7E98-E711-8530-00505688958B       2  2018-04-01   
1792  1792  AECE8386-7E98-E711-8530-00505688958B       1  2018-04-01   
1793  1793  AECE8386-7E98-E711-8530-00505688958B       4  2018-04-01   
1794  1794  AECE8386-7E98-E711-8530-00505688958B       0  2018-04-01   
1795  1795  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-05-01   
1796  1796  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-05-01   
1797  1797  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-05-01   
1798  1798  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-05-01   
1799  1799  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-05-01   
1800  1800  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       0  2018-05-01   
1801  1801  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
1802  1802  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
1803  1803  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       3  2018-05-01   
1804  1804  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-05-01   
1805  1805  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-05-01   
1806  1806  C0B1362A-C378-E511-B4A4-001EC9D5643C       4  2018-05-01   
1807  1807  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-05-01   
1808  1808  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-05-01   
1809  1809  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-05-01   
1810  1810  999F708D-4FE9-E711-B9FF-00505688958B

In [14]:
train_data_mar = train_data_mar[train_data_lastfeb.columns]

In [21]:
train_data_lastfeb['fl_mod'] = 0
train_data_mar['fl_mod'] = 1

In [22]:
train_data_lastmar = pd.concat([train_data_lastfeb, train_data_mar])

In [23]:
train_data_lastmar.shape

(9770, 49)

In [25]:
train_data_lastmar.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

Готовлю данные из марта

In [26]:
train_data_mar.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01        8547.7   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01       13471.7   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01        1136.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01        6598.0   
4  20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01         187.2   

         value          price  mean_sq  mean_fl  month  month_cnt  \
0   811.094601  147387.111111    37.99        9      3         39   
1  1259.443867  138465.811966    57.80        9      3         39   
2   188.162684  171589.583333    23.67       10      3         39   
3   645.633283  134381.707317    80.46        8      3         39   
4    18.758518  182700.000000    93.60        3      3         39   

  Класс объекта  Количество помещений Огорожена территория  \
0        эконом                  1983                  нет   
1        эконом                  1983                  нет   
2        эконом                  1983                  нет   
3        эконом                  1983                  нет   
4       комфорт                  1094                  нет   

   Площадь земельного участка Входные группы  Детский сад  Школа  Поликлиника  \
0                        17.0             да          345    825            0   
1                        17.0             да          345    825            0   
2                        17.0             да          345    825            0   
3                        17.0             да          345    825            0   
4                         6.8             да          150    550            0   

   ФОК Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  \
0    0       нет       да         да                  1           1   
1    0       нет       да         да                  1           1   
2    0       нет       да         да                  1           1   
3    0       нет       да         да                  1           1   
4    1       нет       да         да                  1           1   

   Видеонаблюдение Подземная парковка Двор без машин  Машиномест  \
0                0                 да             да        1800   
1                0                 да             да        1800   
2                0                 да             да        1800   
3                0                 да             да        1800   
4                1                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35

In [27]:
test_data.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  153177.777778    38.00        9      4         40        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          345    825            0    0                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                0                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4        1800                               65357   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                 25533       18.0        12.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  

In [6]:
set(test_data.date1)

{'2018-03-01', '2018-04-01', '2018-05-01'}

In [33]:
min(train_data_mar.value)

0.0

In [34]:
start_square_03 = train_data_mar[['bulk_id', 'spalen', 'start_square', 'value']]
start_square_03['start_square_next'] = start_square_03['start_square'] - start_square_03['value']
start_square_03 = start_square_03.reset_index().drop(['index', 'start_square', 'value'], axis=1)

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  


In [36]:
for itr in range(len(start_square_03)):
    if start_square_03.start_square_next[itr] < 0:
        start_square_03.start_square_next[itr] = 0

/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [39]:
start_square_03

bulk_id  spalen  start_square_next
0    FF3814A9-9F7D-E711-8530-00505688958B       1        7736.605399
1    FF3814A9-9F7D-E711-8530-00505688958B       2       12212.256133
2    FF3814A9-9F7D-E711-8530-00505688958B       0         947.837316
3    FF3814A9-9F7D-E711-8530-00505688958B       3        5952.366717
4    7726CF5A-CC0A-E511-8098-001EC9D56418       3         168.441482
5    72B1CAF6-A2DC-E511-9840-001EC9D56418       2         323.426266
6    35168781-8F60-E611-9523-001EC9D5643C       3        4762.685393
7    35168781-8F60-E611-9523-001EC9D5643C       2          83.524250
8    A8632090-8F60-E611-9523-001EC9D5643C       3        2270.640178
9    A8632090-8F60-E611-9523-001EC9D5643C       2         183.629009
10   50B329EC-1DE2-E511-B953-001EC9D56418       3          38.902555
11   F4BE45B2-AFF2-E611-84D2-001EC9D56418       3        3192.354868
12   F4BE45B2-AFF2-E611-84D2-001EC9D56418       1          73.259781
13   F4BE45B2-AFF2-E611-84D2-001EC9D56418       4           0.000000
14   F4BE45B2-AFF2-E611-84D2-001EC9D56418       2         125.509329
15   832FDFD6-AFF2-E611-84D2-001EC9D56418       3        1687.930028
16   832FDFD6-AFF2-E611-84D2-001EC9D56418       2        2779.884698
17   A93667C6-B147-E311-8507-001EC9D5643C       2         190.143000
18   E522EAD5-DA93-E311-8208-001EC9D56418       1          18.306553
19   5C0E0157-C197-E711-8530-00505688958B       1         794.285111
20   5C0E0157-C197-E711-8530-00505688958B       3        1625.842941
21   5C0E0157-C197-E711-8530-00505688958B       2        2561.927056
22   5C0E0157-C197-E711-8530-00505688958B       0          28.442975
23   BC92BE33-C197-E711-8530-00505688958B       3        1877.604207
24   BC92BE33-C197-E711-8530-00505688958B       2        1235.233817
25   BC92BE33-C197-E711-8530-00505688958B       1         906.711344
26   67127343-C197-E711-8530-00505688958B       3        2546.696792
27   67127343-C197-E711-8530-00505688958B       2        1264.582649
28   67127343-C197-E711-8530-00505688958B       1         788.029050
29   BE6C758E-25F4-E611-84D2-001EC9D56418       2        3906.319326
..                                    ...     ...                ...
496  51917AB1-4566-E711-97EC-001EC9D56418       2        3559.068370
497  51917AB1-4566-E711-97EC-001EC9D56418       3        2391.947305
498  9A2B12C5-4566-E711-97EC-001EC9D56418       3        5160.144503
499  9A2B12C5-4566-E711-97EC-001EC9D56418       2        2719.283811
500  9A2B12C5-4566-E711-97EC-001EC9D56418       1        1397.557850
501  9A2B12C5-4566-E711-97EC-001EC9D56418       0         295.692204
502  9A2B12C5-4566-E711-97EC-001EC9D56418       4         974.074493
503  E51769DC-4566-E711-97EC-001EC9D56418       2        1580.260697
504  E51769DC-4566-E711-97EC-001EC9D56418       1         683.789658
505  E51769DC-4566-E711-97EC-001EC9D56418       3        1373.975957
506  E51769DC-4566-E711-97EC-001EC9D56418       4        2569.085998
507  8CEB3310-63E8-E611-B887-001EC9D5643C       4        1453.300436
508  8CEB3310-63E8-E611-B887-001EC9D5643C       2        6830.396490
509  8CEB3310-63E8-E611-B887-001EC9D5643C       1        4471.467291
510  8CEB3310-63E8-E611-B887-001EC9D5643C       3        6212.872987
511  8CEB3310-63E8-E611-B887-001EC9D5643C       0         193.710000
512  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1           0.000000
513  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2         438.490087
514  C0B1362A-C378-E511-B4A4-001EC9D5643C       2         555.563285
515  C0B1362A-C378-E511-B4A4-001EC9D5643C       3         411.173883
516  C0B1362A-C378-E511-B4A4-001EC9D5643C       1          26.005659
517  999F708D-4FE9-E711-B9FF-00505688958B       0         992.672517
518  999F708D-4FE9-E711-B9FF-00505688958B       1       10022.625658
519  999F708D-4FE9-E711-B9FF-00505688958B       2       16308.574172
520  999F708D-4FE9-E711-B9FF-00505688958B       3       23163.677107
521  999F708D-4FE9-E711-B9FF-00505688958B       4        1371.745460
522  AECE8386-7E98-E711-8530-005

In [38]:
min(start_square_03.start_square_next)

0.0

Готовлю тестовые данные из апреля

In [40]:
test_sub_04 = test_data[test_data['date1']=='2018-04-01']
test_sub_04 = pd.merge(test_sub_04, start_square_03, how='inner', on=['bulk_id', 'spalen'])
test_sub_04 = test_sub_04.rename(index=str, columns={"start_square_next": "start_square"})
test_sub_04['plan'] = test_sub_04['start_square']/test_sub_04['mean_sq']
test_sub_04['plan'] = test_sub_04['plan'].astype(int)

In [41]:
test_sub_04.head()

id                               bulk_id  spalen       date1  \
0   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
1   5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
2   6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
3   7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
4  21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  153177.777778    38.00        9      4         40        эконом   
1  143370.813397    57.79        9      4         40        эконом   
2  179690.000000    24.14        9      4         40        эконом   
3  136624.000000    80.63        8      4         40        эконом   
4  182700.000000    93.60        3      4         40       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Спортивная площадка  \
0             да          345    825            0    0                  да   
1             да          345    825            0    0                  да   
2             да          345    825            0    0                  да   
3             да          345    825            0    0                  да   
4             да          150    550            0    1                  да   

  Автомойка Кладовые Колясочные  Кондиционирование  Вентлияция  Лифт  \
0       нет       да         да                  1           1     1   
1       нет       да         да                  1           1     1   
2       нет       да         да                  1           1     1   
3       нет       да         да                  1           1     1   
4       нет       да         да                  1           1     1   

  Система мусоротведения  Видеонаблюдение Подземная парковка Двор без машин  \
0             контейнеры                0                 да             да   
1             контейнеры                0                 да             да   
2             контейнеры                0                 да             да   
3             контейнеры                0                 да             да   
4             контейнеры                1                 да             да   

   Машиномест  Площадь пром. зоны в радиусе 500 м  \
0        1800                               65357   
1        1800                               65357   
2        1800                               65357   
3        1800                               65357   
4         871                                4740   

   Площадь зеленой зоны в радиусе 500 м  До Кремля  До ТТК(км)  \
0                                 25533       18.0        12.0   
1                                 25533       18.0        12.0   
2                                 25533       18.0        12.0   
3                                 25533       18.0        12.0   
4                                156205       13.0         8.0   

   До Садового(км)  До большой дороги на машине(км)  \
0             16.0                             0.55   
1             16.0                             0.55   
2             16.0                             0.55   
3             16.0                             0.55   
4             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1

In [43]:
test_sub_04['value'] = 0
test_sub_04.drop(['Система мусоротведения', 'Лифт', 'Спортивная площадка'], axis=1, inplace=True)
test_sub_04['fl_mod'] = 1
test_sub_04.to_csv(input_dir + "/test_full_apr_.csv", index=False, columns = train_data_lastmar.columns)

train_data_lastmar.to_csv(input_dir + "/train_full_lastmar_.csv", index=False)

In [13]:
train_data.head()

id                               bulk_id  spalen       date1  start_square  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-10-01       13109.9   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2017-10-01       19898.4   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2017-10-01        2100.0   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2017-10-01        9614.9   
4   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2017-11-01       11947.2   

    value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  1124.5  135633.913043    38.00        8     10         34        эконом   
1  1412.3  128492.419825    58.01        9     10         34        эконом   
2   345.0  158237.634409    22.58       10     10         34        эконом   
3   769.4  123250.000000    78.81        8     10         34        эконом   
4   526.7  139420.634921    37.93        9     11         35        эконом   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1983                  нет                        17.0   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          345    825            0    0       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                0   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да        1800   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                               65357                                 25533   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       18.0        12.0             16.0                             0.55   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                  1.4           0.28   
1                                    1.7                  1.4           0.28   
2                                    1.7                  1.4           0.28   
3                                    1.7                  1.4           0.28   
4                                    1.7                  1.4           0.28   

   До парк

In [14]:
test_sub_03.head()

id                               bulk_id  spalen       date1  \
0   0  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-03-01   
1   1  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-03-01   
2   2  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-03-01   
3   3  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-03-01   
4  20  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-03-01   

           price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0  147387.111111    37.99        9      3         39        эконом   
1  138465.811966    57.80        9      3         39        эконом   
2  171589.583333    23.67       10      3         39        эконом   
3  134381.707317    80.46        8      3         39        эконом   
4  182700.000000    93.60        3      3         39       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          150    550            0    1       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                1   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35           0.45   

   До парка(км)  До парка пешком(км)  Станций метро от кольца  Площадь двора  \
0          0.58                 0.93                        8 

#### Validation

In [4]:
TEST_FILE = input_dir + '/test_full_apr_.csv' #add
CD_FILE = input_dir + '/train_full_feat.txt'

train_data = pd.read_csv(input_dir + "/train_full_lastmar_.csv")
test_data = pd.read_csv(TEST_FILE)

In [7]:
test_data.head()

id                               bulk_id  spalen       date1  start_square  \
0   4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   7736.605399   
1   5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01  12212.256133   
2   6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01    947.837316   
3   7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   5952.366717   
4  21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01    168.441482   

   value          price  mean_sq  mean_fl  month  month_cnt Класс объекта  \
0      0  153177.777778    38.00        9      4         40        эконом   
1      0  143370.813397    57.79        9      4         40        эконом   
2      0  179690.000000    24.14        9      4         40        эконом   
3      0  136624.000000    80.63        8      4         40        эконом   
4      0  182700.000000    93.60        3      4         40       комфорт   

   Количество помещений Огорожена территория  Площадь земельного участка  \
0                  1983                  нет                        17.0   
1                  1983                  нет                        17.0   
2                  1983                  нет                        17.0   
3                  1983                  нет                        17.0   
4                  1094                  нет                         6.8   

  Входные группы  Детский сад  Школа  Поликлиника  ФОК Автомойка Кладовые  \
0             да          345    825            0    0       нет       да   
1             да          345    825            0    0       нет       да   
2             да          345    825            0    0       нет       да   
3             да          345    825            0    0       нет       да   
4             да          150    550            0    1       нет       да   

  Колясочные  Кондиционирование  Вентлияция  Видеонаблюдение  \
0         да                  1           1                0   
1         да                  1           1                0   
2         да                  1           1                0   
3         да                  1           1                0   
4         да                  1           1                1   

  Подземная парковка Двор без машин  Машиномест  \
0                 да             да        1800   
1                 да             да        1800   
2                 да             да        1800   
3                 да             да        1800   
4                 да             да         871   

   Площадь пром. зоны в радиусе 500 м  Площадь зеленой зоны в радиусе 500 м  \
0                               65357                                 25533   
1                               65357                                 25533   
2                               65357                                 25533   
3                               65357                                 25533   
4                                4740                                156205   

   До Кремля  До ТТК(км)  До Садового(км)  До большой дороги на машине(км)  \
0       18.0        12.0             16.0                             0.55   
1       18.0        12.0             16.0                             0.55   
2       18.0        12.0             16.0                             0.55   
3       18.0        12.0             16.0                             0.55   
4       13.0         8.0             11.0                             0.69   

   До удобной авторазвязки на машине(км)  До метро пешком(км)  До промки(км)  \
0                                    1.7                 1.40           0.28   
1                                    1.7                 1.40           0.28   
2                                    1.7                 1.40           0.28   
3                                    1.7                 1.40           0.28   
4                                    7.0                 0.35           0.45   

   До парка(км) 

In [8]:
K = 10

kf = KFold(n_splits=K, random_state=42, shuffle=True)
kf.get_n_splits(range(len(train_data)))

print(kf)  

for i, (train_index, valid_index) in enumerate(kf.split(range(len(train_data)))):
    train = train_data.loc[train_index]
    valid = train_data.loc[valid_index]

    train.to_csv(input_dir + f"/train_{i}.csv",index=False)
    valid.to_csv(input_dir + f"/valid_{i}.csv",index=False)

KFold(n_splits=10, random_state=42, shuffle=True)


#### Fit and Predict

In [9]:
test_pool = Pool(TEST_FILE, column_description=CD_FILE, has_header=True, delimiter=",")

In [10]:
iterations = 5000
learning_rate = 0.05
depth = 8
random_seed = 42

Regressors = [
    CatBoostRegressor(iterations=iterations, learning_rate=learning_rate, depth=depth, random_seed=random_seed)
]

In [11]:
def FitOnKFolds(model):
    cum_y_test = np.zeros((len(test_data), 1))
    pred_y_train = np.zeros((len(train_data), 1))
    
    for i in range(K):
        TRAIN_FILE = input_dir + f'/train_{i}.csv'
        VAL_FILE = input_dir + f'/valid_{i}.csv'
        
        train_pool = Pool(TRAIN_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        val_pool = Pool(VAL_FILE, column_description=CD_FILE, has_header=True, delimiter=",")
        
        model.fit(train_pool, eval_set = val_pool)
        pickle.dump(model, open(input_dir + f'mod_full_feat_lastfeb_{i}.sav', 'wb'))
        
        pred = model.predict(test_pool)
        cum_y_test += pred.reshape((len(test_data),1))
        
        pred = model.predict(val_pool)
        df = pd.read_csv(VAL_FILE)
        pred_y_train[df.id] = pred.reshape((len(df),1))
        
    return (cum_y_test/K).clip(int(min(train_data.value)), int(max(train_data.value))).reshape(-1),\
        sqrt(mean_squared_error(list(train_data['value']), list(pred_y_train)))

In [12]:
def write_ans(fl_name, y_test):
    dict_ans = defaultdict(list)
    dict_ans['id'] = list(range(len(y_test)))
    dict_ans['value'] = list(y_test)
    df_ans = pd.DataFrame.from_dict(dict_ans)
    df_ans.to_csv(sub_dir+'/'+fl_name+'.csv', index=False)
    return 'Answer /%s succesfully writed' % fl_name

In [13]:
%%time

vec_qual = []

for itr, model in enumerate(Regressors):
    y_test, qual = FitOnKFolds(model)
    vec_qual.append(qual)
    write_ans(f'sub_apr_ctb_itr={iterations}_lr={learning_rate}_depth={depth}_fld={K}_{itr}vers', y_test)

0:	learn: 426.5123263	test: 438.2616696	best: 438.2616696 (0)	total: 113ms	remaining: 9m 22s
1:	learn: 415.1746533	test: 425.9895356	best: 425.9895356 (1)	total: 160ms	remaining: 6m 38s
2:	learn: 405.2417917	test: 415.4687466	best: 415.4687466 (2)	total: 184ms	remaining: 5m 6s
3:	learn: 396.0662013	test: 405.8766162	best: 405.8766162 (3)	total: 231ms	remaining: 4m 48s
4:	learn: 387.3203575	test: 396.3394588	best: 396.3394588 (4)	total: 245ms	remaining: 4m 4s
5:	learn: 378.2722210	test: 386.6384854	best: 386.6384854 (5)	total: 296ms	remaining: 4m 6s
6:	learn: 371.2710005	test: 378.9993249	best: 378.9993249 (6)	total: 306ms	remaining: 3m 37s
7:	learn: 363.8919367	test: 371.3739842	best: 371.3739842 (7)	total: 368ms	remaining: 3m 49s
8:	learn: 357.3067946	test: 364.3704626	best: 364.3704626 (8)	total: 415ms	remaining: 3m 50s
9:	learn: 350.5940609	test: 356.9346010	best: 356.9346010 (9)	total: 461ms	remaining: 3m 50s
10:	learn: 344.3687323	test: 350.3913532	best: 350.3913532 (10)	total: 51

88:	learn: 226.6770952	test: 241.7727585	best: 241.7727585 (88)	total: 4.8s	remaining: 4m 25s
89:	learn: 225.7567254	test: 240.9339544	best: 240.9339544 (89)	total: 4.85s	remaining: 4m 24s
90:	learn: 225.1920118	test: 240.8296241	best: 240.8296241 (90)	total: 4.9s	remaining: 4m 24s
91:	learn: 224.7144509	test: 240.4471311	best: 240.4471311 (91)	total: 4.95s	remaining: 4m 24s
92:	learn: 224.3183808	test: 240.2347731	best: 240.2347731 (92)	total: 4.99s	remaining: 4m 23s
93:	learn: 223.6528619	test: 239.3995588	best: 239.3995588 (93)	total: 5.04s	remaining: 4m 23s
94:	learn: 223.1378902	test: 238.9690603	best: 238.9690603 (94)	total: 5.09s	remaining: 4m 22s
95:	learn: 222.8021342	test: 238.7781997	best: 238.7781997 (95)	total: 5.14s	remaining: 4m 22s
96:	learn: 222.6694662	test: 238.7499715	best: 238.7499715 (96)	total: 5.16s	remaining: 4m 20s
97:	learn: 222.3697339	test: 238.5229414	best: 238.5229414 (97)	total: 5.2s	remaining: 4m 20s
98:	learn: 221.5639959	test: 238.1311818	best: 238.13

176:	learn: 197.2125928	test: 221.9236322	best: 221.9236322 (176)	total: 9.59s	remaining: 4m 21s
177:	learn: 196.8884287	test: 221.5791330	best: 221.5791330 (177)	total: 9.63s	remaining: 4m 20s
178:	learn: 196.8879497	test: 221.5788678	best: 221.5788678 (178)	total: 9.64s	remaining: 4m 19s
179:	learn: 196.7061226	test: 221.5947219	best: 221.5788678 (178)	total: 9.68s	remaining: 4m 19s
180:	learn: 196.6194164	test: 221.6076808	best: 221.5788678 (178)	total: 9.74s	remaining: 4m 19s
181:	learn: 196.3443972	test: 221.4860689	best: 221.4860689 (181)	total: 9.79s	remaining: 4m 19s
182:	learn: 196.3036986	test: 221.4805343	best: 221.4805343 (182)	total: 9.85s	remaining: 4m 19s
183:	learn: 196.0709221	test: 221.3573363	best: 221.3573363 (183)	total: 9.91s	remaining: 4m 19s
184:	learn: 195.8685150	test: 221.1512224	best: 221.1512224 (184)	total: 9.97s	remaining: 4m 19s
185:	learn: 195.5853919	test: 220.9868219	best: 220.9868219 (185)	total: 10s	remaining: 4m 19s
186:	learn: 195.3559607	test: 22

261:	learn: 180.2551580	test: 213.1948630	best: 213.1948630 (261)	total: 15s	remaining: 4m 31s
262:	learn: 180.1223527	test: 213.1821894	best: 213.1821894 (262)	total: 15s	remaining: 4m 30s
263:	learn: 179.8009168	test: 213.0369743	best: 213.0369743 (263)	total: 15.1s	remaining: 4m 31s
264:	learn: 179.6622918	test: 213.0014302	best: 213.0014302 (264)	total: 15.2s	remaining: 4m 31s
265:	learn: 179.5835052	test: 212.9506705	best: 212.9506705 (265)	total: 15.2s	remaining: 4m 31s
266:	learn: 179.4598793	test: 212.9295496	best: 212.9295496 (266)	total: 15.3s	remaining: 4m 31s
267:	learn: 179.1988896	test: 212.7087798	best: 212.7087798 (267)	total: 15.4s	remaining: 4m 31s
268:	learn: 178.9616356	test: 212.5585172	best: 212.5585172 (268)	total: 15.4s	remaining: 4m 31s
269:	learn: 178.7910624	test: 212.4944727	best: 212.4944727 (269)	total: 15.5s	remaining: 4m 31s
270:	learn: 178.5596484	test: 212.3666432	best: 212.3666432 (270)	total: 15.5s	remaining: 4m 31s
271:	learn: 178.4126821	test: 212.

349:	learn: 168.0687462	test: 207.2247570	best: 207.1451563 (345)	total: 20.7s	remaining: 4m 34s
350:	learn: 167.9303848	test: 207.2521986	best: 207.1451563 (345)	total: 20.8s	remaining: 4m 35s
351:	learn: 167.8601412	test: 207.2066873	best: 207.1451563 (345)	total: 20.9s	remaining: 4m 35s
352:	learn: 167.7488462	test: 207.1065495	best: 207.1065495 (352)	total: 21s	remaining: 4m 35s
353:	learn: 167.6353719	test: 207.1346756	best: 207.1065495 (352)	total: 21s	remaining: 4m 35s
354:	learn: 167.5128725	test: 207.0192327	best: 207.0192327 (354)	total: 21.1s	remaining: 4m 36s
355:	learn: 167.4773100	test: 207.0601620	best: 207.0192327 (354)	total: 21.2s	remaining: 4m 35s
356:	learn: 166.9478010	test: 206.5890584	best: 206.5890584 (356)	total: 21.2s	remaining: 4m 35s
357:	learn: 166.8305392	test: 206.4877131	best: 206.4877131 (357)	total: 21.3s	remaining: 4m 35s
358:	learn: 166.7673190	test: 206.4669378	best: 206.4669378 (358)	total: 21.3s	remaining: 4m 35s
359:	learn: 166.6971634	test: 206.

...

4650:	learn: 76.3656660	test: 178.0021955	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.9s
4651:	learn: 76.3612283	test: 178.0000301	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.9s
4652:	learn: 76.3603406	test: 178.0049415	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.8s
4653:	learn: 76.3573630	test: 178.0132255	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.8s
4654:	learn: 76.3563463	test: 178.0122408	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.7s
4655:	learn: 76.3552790	test: 178.0008052	best: 177.9987082 (4649)	total: 4m 12s	remaining: 18.7s
4656:	learn: 76.3532045	test: 177.9918562	best: 177.9918562 (4656)	total: 4m 12s	remaining: 18.6s
4657:	learn: 76.3531042	test: 177.9912631	best: 177.9912631 (4657)	total: 4m 12s	remaining: 18.6s
4658:	learn: 76.3327054	test: 177.9826438	best: 177.9826438 (4658)	total: 4m 12s	remaining: 18.5s
4659:	learn: 76.3195525	test: 177.9748732	best: 177.9748732 (4659)	total: 4m 12s	remaining: 18.4s
4660:	learn: 76.3193

4737:	learn: 75.8691233	test: 177.9158046	best: 177.8981045 (4703)	total: 4m 16s	remaining: 14.2s
4738:	learn: 75.8621109	test: 177.9204776	best: 177.8981045 (4703)	total: 4m 16s	remaining: 14.2s
4739:	learn: 75.8549022	test: 177.9258497	best: 177.8981045 (4703)	total: 4m 16s	remaining: 14.1s
4740:	learn: 75.8544160	test: 177.9256693	best: 177.8981045 (4703)	total: 4m 17s	remaining: 14s
4741:	learn: 75.8393710	test: 177.9331556	best: 177.8981045 (4703)	total: 4m 17s	remaining: 14s
4742:	learn: 75.8380942	test: 177.9331321	best: 177.8981045 (4703)	total: 4m 17s	remaining: 13.9s
4743:	learn: 75.8190056	test: 177.9405925	best: 177.8981045 (4703)	total: 4m 17s	remaining: 13.9s
4744:	learn: 75.8189149	test: 177.9399194	best: 177.8981045 (4703)	total: 4m 17s	remaining: 13.8s
4745:	learn: 75.8153304	test: 177.9417324	best: 177.8981045 (4703)	total: 4m 17s	remaining: 13.8s
4746:	learn: 75.8106428	test: 177.9612465	best: 177.8981045 (4703)	total: 4m 17s	remaining: 13.7s
4747:	learn: 75.8063989	

4821:	learn: 75.3026210	test: 177.8340620	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.65s
4822:	learn: 75.2924191	test: 177.8194423	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.59s
4823:	learn: 75.2884273	test: 177.8240542	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.54s
4824:	learn: 75.2883738	test: 177.8240683	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.48s
4825:	learn: 75.2879581	test: 177.8239113	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.43s
4826:	learn: 75.2823040	test: 177.8194850	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.38s
4827:	learn: 75.2809309	test: 177.8220943	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.32s
4828:	learn: 75.2799565	test: 177.8224094	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.27s
4829:	learn: 75.2695324	test: 177.8383584	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.21s
4830:	learn: 75.2608959	test: 177.8302676	best: 177.8101779 (4814)	total: 4m 21s	remaining: 9.16s
4831:	learn: 75.2599

4906:	learn: 74.8150520	test: 177.6541489	best: 177.6351686 (4900)	total: 4m 25s	remaining: 5.04s
4907:	learn: 74.8139581	test: 177.6545907	best: 177.6351686 (4900)	total: 4m 25s	remaining: 4.98s
4908:	learn: 74.8135288	test: 177.6528849	best: 177.6351686 (4900)	total: 4m 25s	remaining: 4.93s
4909:	learn: 74.8020561	test: 177.6521946	best: 177.6351686 (4900)	total: 4m 25s	remaining: 4.87s
4910:	learn: 74.7917859	test: 177.6525444	best: 177.6351686 (4900)	total: 4m 25s	remaining: 4.82s
4911:	learn: 74.7886917	test: 177.6456735	best: 177.6351686 (4900)	total: 4m 26s	remaining: 4.77s
4912:	learn: 74.7755588	test: 177.6508844	best: 177.6351686 (4900)	total: 4m 26s	remaining: 4.71s
4913:	learn: 74.7594244	test: 177.6714453	best: 177.6351686 (4900)	total: 4m 26s	remaining: 4.66s
4914:	learn: 74.7576992	test: 177.6693224	best: 177.6351686 (4900)	total: 4m 26s	remaining: 4.6s
4915:	learn: 74.7357718	test: 177.6530915	best: 177.6351686 (4900)	total: 4m 26s	remaining: 4.55s
4916:	learn: 74.71282

4992:	learn: 74.1108010	test: 177.5903458	best: 177.5639162 (4977)	total: 4m 30s	remaining: 379ms
4993:	learn: 74.1080666	test: 177.5867172	best: 177.5639162 (4977)	total: 4m 30s	remaining: 325ms
4994:	learn: 74.1050421	test: 177.5855981	best: 177.5639162 (4977)	total: 4m 30s	remaining: 271ms
4995:	learn: 74.0800581	test: 177.5823228	best: 177.5639162 (4977)	total: 4m 30s	remaining: 216ms
4996:	learn: 74.0796180	test: 177.5831852	best: 177.5639162 (4977)	total: 4m 30s	remaining: 162ms
4997:	learn: 74.0777628	test: 177.5898464	best: 177.5639162 (4977)	total: 4m 30s	remaining: 108ms
4998:	learn: 74.0586248	test: 177.5785114	best: 177.5639162 (4977)	total: 4m 30s	remaining: 54.1ms
4999:	learn: 74.0578031	test: 177.5785537	best: 177.5639162 (4977)	total: 4m 30s	remaining: 0us

bestTest = 177.5639162
bestIteration = 4977

Shrink model to first 4978 iterations.
CPU times: user 2h 38min 20s, sys: 4min 55s, total: 2h 43min 16s
Wall time: 45min 17s


In [14]:
print(vec_qual)
#model = pickle.load(open(input_dir + f'mod_part_feat_{i}.sav', 'rb'))

[213.20321364282523]


In [15]:
y_test

array([7.16692757e+02, 1.11232148e+03, 1.89787947e+02, 5.90209240e+02,
       3.33593563e+01, 1.63252360e+02, 3.44689213e+02, 1.32821586e+02,
       3.65576912e+02, 2.02299590e+02, 4.71611791e+02, 6.73248256e+01,
       3.86734509e+01, 5.43612411e+01, 3.33690415e+02, 9.90735438e+02,
       4.54139896e+01, 4.22670158e+01, 9.60371813e+01, 1.98808289e+02,
       1.94009984e+02, 6.20177646e+02, 2.72277319e+02, 1.93956861e+02,
       3.71911338e+02, 1.85968713e+02, 2.72517596e+02, 3.50989452e+02,
       6.49218182e+02, 4.70131870e+01, 1.44055923e+02, 2.51356237e+02,
       1.42609737e+02, 1.27309096e+02, 0.00000000e+00, 1.72614175e+02,
       4.41503625e+02, 1.79108358e+02, 2.94862146e+01, 1.09875205e+02,
       3.81485880e+02, 2.50898526e+02, 9.31119533e+01, 2.54171810e+01,
       8.70672959e+02, 5.56820323e+02, 1.30315452e+03, 1.67391972e+01,
       4.49941472e+02, 1.52564619e+02, 3.06528730e+02, 1.32342569e+01,
       4.49918181e+02, 1.84091843e+02, 6.39439538e+01, 1.09570129e+02,
      

In [16]:
test_data_apr = test_data

In [17]:
test_data_apr['value'] = list(y_test)

In [18]:
test_data_apr

id                               bulk_id  spalen       date1  \
0       4  FF3814A9-9F7D-E711-8530-00505688958B       1  2018-04-01   
1       5  FF3814A9-9F7D-E711-8530-00505688958B       2  2018-04-01   
2       6  FF3814A9-9F7D-E711-8530-00505688958B       0  2018-04-01   
3       7  FF3814A9-9F7D-E711-8530-00505688958B       3  2018-04-01   
4      21  7726CF5A-CC0A-E511-8098-001EC9D56418       3  2018-04-01   
5      58  72B1CAF6-A2DC-E511-9840-001EC9D56418       2  2018-04-01   
6      59  35168781-8F60-E611-9523-001EC9D5643C       3  2018-04-01   
7      60  35168781-8F60-E611-9523-001EC9D5643C       2  2018-04-01   
8      61  A8632090-8F60-E611-9523-001EC9D5643C       3  2018-04-01   
9      62  A8632090-8F60-E611-9523-001EC9D5643C       2  2018-04-01   
10     63  F4BE45B2-AFF2-E611-84D2-001EC9D56418       3  2018-04-01   
11     64  F4BE45B2-AFF2-E611-84D2-001EC9D56418       4  2018-04-01   
12     65  F4BE45B2-AFF2-E611-84D2-001EC9D56418       1  2018-04-01   
13     66  F4BE45B2-AFF2-E611-84D2-001EC9D56418       2  2018-04-01   
14     67  832FDFD6-AFF2-E611-84D2-001EC9D56418       3  2018-04-01   
15     68  832FDFD6-AFF2-E611-84D2-001EC9D56418       2  2018-04-01   
16     69  A93667C6-B147-E311-8507-001EC9D5643C       2  2018-04-01   
17     70  E522EAD5-DA93-E311-8208-001EC9D56418       1  2018-04-01   
18     71  5C0E0157-C197-E711-8530-00505688958B       0  2018-04-01   
19     72  5C0E0157-C197-E711-8530-00505688958B       3  2018-04-01   
20     73  5C0E0157-C197-E711-8530-00505688958B       1  2018-04-01   
21     74  5C0E0157-C197-E711-8530-00505688958B       2  2018-04-01   
22     84  BC92BE33-C197-E711-8530-00505688958B       3  2018-04-01   
23     85  BC92BE33-C197-E711-8530-00505688958B       1  2018-04-01   
24     86  BC92BE33-C197-E711-8530-00505688958B       2  2018-04-01   
25     87  67127343-C197-E711-8530-00505688958B       1  2018-04-01   
26     88  67127343-C197-E711-8530-00505688958B       3  2018-04-01   
27     89  67127343-C197-E711-8530-00505688958B       2  2018-04-01   
28    125  BE6C758E-25F4-E611-84D2-001EC9D56418       2  2018-04-01   
29    126  BE6C758E-25F4-E611-84D2-001EC9D56418       1  2018-04-01   
..    ...                                   ...     ...         ...   
459  1725  51917AB1-4566-E711-97EC-001EC9D56418       2  2018-04-01   
460  1726  51917AB1-4566-E711-97EC-001EC9D56418       3  2018-04-01   
461  1727  9A2B12C5-4566-E711-97EC-001EC9D56418       3  2018-04-01   
462  1728  9A2B12C5-4566-E711-97EC-001EC9D56418       2  2018-04-01   
463  1729  9A2B12C5-4566-E711-97EC-001EC9D56418       1  2018-04-01   
464  1730  9A2B12C5-4566-E711-97EC-001EC9D56418       0  2018-04-01   
465  1731  9A2B12C5-4566-E711-97EC-001EC9D56418       4  2018-04-01   
466  1732  E51769DC-4566-E711-97EC-001EC9D56418       2  2018-04-01   
467  1733  E51769DC-4566-E711-97EC-001EC9D56418       1  2018-04-01   
468  1734  E51769DC-4566-E711-97EC-001EC9D56418       3  2018-04-01   
469  1735  E51769DC-4566-E711-97EC-001EC9D56418       4  2018-04-01   
470  1773  8CEB3310-63E8-E611-B887-001EC9D5643C       4  2018-04-01   
471  1774  8CEB3310-63E8-E611-B887-001EC9D5643C       2  2018-04-01   
472  1775  8CEB3310-63E8-E611-B887-001EC9D5643C       1  2018-04-01   
473  1776  8CEB3310-63E8-E611-B887-001EC9D5643C       3  2018-04-01   
474  1777  8CEB3310-63E8-E611-B887-001EC9D5643C       0  2018-04-01   
475  1778  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       2  2018-04-01   
476  1779  8B5D0C0E-C378-E511-B4A4-001EC9D5643C       1  2018-04-01   
477  1782  C0B1362A-C378-E511-B4A4-001EC9D5643C       2  2018-04-01   
478  1783  C0B1362A-C378-E511-B4A4-001EC9D5643C       3  2018-04-01   
479  1785  C0B1362A-C378-E511-B4A4-001EC9D5643C       1  2018-04-01   
480  1786  999F708D-4FE9-E711-B9FF-00505688958B       0  2018-04-01   
481  1787  999F708D-4FE9-E711-B9FF-00505688958B       1  2018-04-01   
482  1788  999F708D-4FE9-E711-B9FF-00505688958B       2  2018-04-01   
483  1789  999F708D-4FE9-E711-B

#### Unload Data

In [19]:
test_data_apr.to_csv(sub_dir + f"/subsub_full_feat_apr.csv")